In this notebook we will cluster a set molecules using the [Taylor-Butina](https://pubs.acs.org/doi/pdf/10.1021/ci9803381) clustering method.  

Install the necessary Python libraries

In [23]:
!pip install pandas rdkit_pypi seaborn tqdm mols2grid

Import the necessary Python libraries

In [10]:
import pandas as pd
from rdkit import Chem
from rdkit import DataStructs
from rdkit.ML.Cluster import Butina
from rdkit.Chem import rdMolDescriptors as rdmd
from rdkit.Chem import Descriptors
from tqdm.auto import tqdm
import mols2grid

In [8]:
tqdm.pandas()

Define a function to do the clustering.  While the RDKit has a function to do the clustering, we still need to cacluate fingerprints and assign cluster ids. This function performs the following steps. 
1. Calculate fingerprints for each molecule in mol_list
2. Calculate the similarity of every molecule to every othter molecule (all pairs)
3. Create a distance matrix containing 1-similarity for each pairwise similarity value
4. Assign a cluster id to each molecule

In [2]:
def butina_cluster(mol_list,cutoff=0.35):
    fp_list = [rdmd.GetMorganFingerprintAsBitVect(m, 3, nBits=2048) for m in mol_list]
    dists = []
    nfps = len(fp_list)
    for i in range(1,nfps):
        sims = DataStructs.BulkTanimotoSimilarity(fp_list[i],fp_list[:i])
        dists.extend([1-x for x in sims])
    mol_clusters = Butina.ClusterData(dists,nfps,cutoff,isDistData=True)
    cluster_id_list = [0]*nfps
    for idx,cluster in enumerate(mol_clusters,1):
        for member in cluster:
            cluster_id_list[member] = idx
    return cluster_id_list

Read a csv file with the input data.  This data contains a set of ERK2 inhibitors and decoy molecules from the [DUD-E database](http://dude.docking.org/targets/mk01).  

In [3]:
df = pd.read_csv("https://raw.githubusercontent.com/PatWalters/practical_cheminformatics_tutorials/main/data/dude_erk2_mk01.csv")

Let's look at the first few lines of the dataframe.  Note that there are three columns, SMILES, molecule name, and an indicator variable "is_active" where 1 represents an active compound and 0 represents a decoy. 

In [4]:
df.head()

Unnamed: 0                                             SMILES      ID  \
0           0  Cn1ccnc1Sc2ccc(cc2Cl)Nc3c4cc(c(cc4ncc3C#N)OCCC...  168691   
1           1  C[C@@]12[C@@H]([C@@H](CC(O1)n3c4ccccc4c5c3c6n2...   86358   
2           2  Cc1cnc(nc1c2cc([nH]c2)C(=O)N[C@H](CO)c3cccc(c3...  575087   
3           3  Cc1cnc(nc1c2cc([nH]c2)C(=O)N[C@H](CO)c3cccc(c3...  575065   
4           4  Cc1cnc(nc1c2cc([nH]c2)C(=O)N[C@H](CO)c3cccc(c3...  575047   

   is_active  
0          1  
1          1  
2          1  
3          1  
4          1

We can use mols2grid to get a quick look at our dataframe.

In [5]:
mols2grid.display(df)

Add an RDKit molecule column to the dataframe. 

In [11]:
df['mol'] = df.SMILES.progress_apply(Chem.MolFromSmiles)

  0%|          | 0/4629 [00:00<?, ?it/s]

Cluster the molecules in the dataframe and assign the cluster id to a new column. 

In [12]:
%time df['Cluster'] = butina_cluster(df.mol.values)

CPU times: user 4.07 s, sys: 251 ms, total: 4.32 s
Wall time: 4.34 s


View the dataframe with the new **Cluster** column

In [14]:
mols2grid.display(df,subset=["img","ID","Cluster"])

Let's look at how we could select the molecule from each cluster with the lowest LogP.  First we'll calculate the LogP for each molecule and put these values into a new column called "logP".

In [15]:
df["logP"] = df.mol.progress_apply(Descriptors.MolLogP)

  0%|          | 0/4629 [00:00<?, ?it/s]

View the dataframe with the LogP added. Note how we use the mols2grid **transform** function to set the number of decimal places for LogP.   Try removing this and see what happens, it's not pretty. 

In [17]:
mols2grid.display(df,subset=["img","ID","Cluster","logP"],transform={"logP": lambda x: f"{x:.2f}"})

Sort the dataframe, first by **Cluster** then by **logP**.

In [18]:
df.sort_values(["Cluster","logP"],inplace=True)

In [19]:
mols2grid.display(df,subset=["img","ID","Cluster","logP"],transform={"logP": lambda x: f"{x:.2f}"})

Now let's create a new dataframe containing only the molecule from each cluster with the lowest LogP.  Since we have already sorted the dataframe by cluster id and LogP, we can simply use the [drop_duplicates](https://pandas.pydata.org/pandas-docs/stable/reference/api/pandas.DataFrame.drop_duplicates.html) method to drop all but the first row in each cluster. 

In [21]:
df_unique = df.drop_duplicates("Cluster")

In [22]:
mols2grid.display(df_unique,subset=["img","ID","Cluster","logP"],transform={"logP": lambda x: f"{x:.2f}"})